# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [20 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [3]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f6f709c95d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 12:30:00, Parking_time: 24, Leaving_time: 2022-01-02 12:30:00, SOC: 0.48812244053865134, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1043, Arrival time: 2022-12-30 15:30:00, Parking_time: 24, Leaving_time: 2022-12-31 15:30:00, SOC: 0.5530960042694243, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20700.93 , Grid_used_en=kWh  37514.32 , RE-to-vehicle_unused_en=kWh  16813.39 , Total_selling_cost=€  831.19 , Grid_cost=€  1315.5 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08


In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21605.19 , Grid_used_en(grid-import)=38857.82kWh , Total_demand=71886.69kWh , autarky-rate=45.9 , RE-to-vehicle_unused_en(grid-export)=17252.63kWh , Total_supply=50281.51kWh , self-consump.rate=65.7 , Grid_cost=€  1361.1 , Total_selling_cost=€  869.41 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_autarky()

In [12]:
#env.plot_Elvis_results()

In [13]:
#env.plot_VPP_results()

In [14]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_VPP_Elvis_comparison()

In [16]:
#env.plot_rewards_results()

In [17]:
#env.plot_rewards_stats()

In [18]:
env.plot_EVs_kpi()

In [19]:
env.plot_actions_kpi()

In [20]:
env.plot_load_kpi()

In [21]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [22]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [23]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [24]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20809.03 , Grid_used_en(grid-import)=38904.65kWh , Total_demand=71054.02kWh , autarky-rate=45.2 , RE-to-vehicle_unused_en(grid-export)=18095.62kWh , Total_supply=50244.99kWh , self-consump.rate=64.0 , Grid_cost=€  1382.24 , Total_selling_cost=€  860.04 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3962.85 , Grid_used_en(grid-import)=2062.32kWh , Total_demand=58939.1kWh , autarky-rate=96.5 , RE-to-vehicle_unused_en(grid-export)=6025.17kWh , Total_supply=62901.95kWh , self-consump.rate=90.4 , Total_selling_cost=€  -86.39 , Grid_cost=€  69.55 
 EV_INFO: Av.EV_energy_leaving=kWh  66.94 , Std.EV_energy_leaving=kWh  23.59 , EV_departures =  1039 , EV_queue_left =  1
SCORE:  Cumulative_reward= 402167.72 - Step_rewars (load_t= 362680.31, EVs_en

In [25]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
VPP_table.head(15000)

0          1          2          3              EVs_id  \
time                                                                            
2022-01-01 00:00:00  0.0   0.000000  47.995525   0.000000        [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0   0.000000  47.515820   0.000000     [0, 0, 3129, 0]   
2022-01-01 00:30:00  0.0   0.000000  47.109158   0.000000     [0, 0, 3129, 0]   
2022-01-01 00:45:00  0.0   0.000000  46.671268   0.000000     [0, 0, 3129, 0]   
2022-01-01 01:00:00  0.0   0.000000  46.247360   0.000000     [0, 0, 3129, 0]   
...                  ...        ...        ...        ...                 ...   
2022-06-06 04:45:00  0.0  88.629120   0.000000  91.953125  [0, 3598, 0, 3597]   
2022-06-06 05:00:00  0.0  90.139038   0.000000  93.463043  [0, 3598, 0, 3597]   
2022-06-06 05:15:00  0.0  91.648605   0.000000  94.972610  [0, 3598, 0, 3597]   
2022-06-06 05:30:00  0.0  93.138214   0.000000  96.462219  [0, 3598, 0, 3597]   
2022-06-06 05:45:00  0.0  94.601822   0.000000  97.925827  [0, 3598, 0, 3597]   

                          actions                    mask_truth  \
time                                                              
2022-01-01 00:00:00  [2, 2, 2, 2]  [False, False, False, False]   
2022-01-01 00:15:00  [2, 0, 2, 2]    [False, True, True, False]   
2022-01-01 00:30:00  [2, 0, 2, 2]    [False, True, True, False]   
2022-01-01 00:45:00  [2, 0, 2, 2]    [False, True, True, False]   
2022-01-01 01:00:00  [2, 0, 2, 2]    [False, True, True, False]   
...                           ...                           ...   
2022-06-06 04:45:00  [2, 1, 0, 1]    [False, True, True, False]   
2022-06-06 05:00:00  [2, 1, 0, 1]    [False, True, True, False]   
2022-06-06 05:15:00  [2, 1, 0, 1]    [False, True, True, False]   
2022-06-06 05:30:00  [2, 1, 0, 1]    [False, True, True, False]   
2022-06-06 05:45:00  [2, 1, 0, 1]    [False, True, True, False]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000           0.000000  1.612587         15.0   
2022-01-01 00:15:00        0.000000          -1.918819  0.000000         15.0   
2022-01-01 00:30:00        0.000000          -1.626645  0.000000         15.0   
2022-01-01 00:45:00        0.000000          -1.751563  0.000000         15.0   
2022-01-01 01:00:00        0.000000          -1.695639  0.000000         15.0   
...                             ...                ...       ...          ...   
2022-06-06 04:45:00        9.601403           0.000000  0.000000         15.0   
2022-06-06 05:00:00       12.079361           0.000000  0.000000         15.0   
2022-06-06 05:15:00       12.076530           0.000000  0.000000         15.0   
2022-06-06 05:30:00       11.916848           0.000000  0.000000         15.0   
2022-06-06 05:45:00       11.708847           0.000000  0.000000         15.0   

                     EV_reward  rewards  
time                                     
2022-01-01 00:00:00        0.0     15.0  
2022-01-01 00:15:00        0.0     15.0  
2022-01-01 00:30:00        0.0     15.0  
2022-01-01 00:45:00        0.0     15.0  
2022-01-01 01:00:00        0.0     15.0  
...                        ...      ...  
2022-06-06 04:45:00        0.0     15.0  
2022-06-06 05:00:00        0.0     15.0  
2022-06-06 05:15:00        0.0     15.0  
2022-06-06 05:30:00        0.0     15.0  
2022-06-06 05:45:00        0.0     15.0  

[15000 rows x 13 columns]

In [27]:
env.plot_VPP_autarky()

In [28]:
#env.plot_Elvis_results()

In [29]:
#env.plot_VPP_results()

In [30]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_VPP_Elvis_comparison()

In [32]:
#env.plot_rewards_results()

In [33]:
env.plot_rewards_stats()

In [34]:
env.plot_EVs_kpi()

In [35]:
env.plot_load_kpi()

In [36]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [37]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 04:00:00, Parking_time: 23.669922441556864, Leaving_time: 2022-01-02 03:40:11.720790, SOC: 0.754499445584628, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 11:00:00, Parking_time: 24, Leaving_time: 2023-01-01 11:00:00, SOC: 0.7567845353065289, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12158.33 , Grid_used_en=kWh  34358.04 , RE-to-vehicle_unused_en=kWh  22199.71 , Total_selling_cost=€  594.7 , Grid_cost=€  1496.37 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [38]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
#plot_VPP_input_data.show()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12545.05 , Grid_used_en(grid-import)=34417.96kWh , Total_demand=63173.78kWh , autarky-rate=45.5 , RE-to-vehicle_unused_en(grid-export)=21872.91kWh , Total_supply=50628.73kWh , self-consump.rate=56.8 , Grid_cost=€  1525.42 , Total_selling_cost=€  635.68 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....


In [39]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [40]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12927.54 , Grid_used_en(grid-import)=35355.17kWh , Total_demand=63567.77kWh , autarky-rate=44.4 , RE-to-vehicle_unused_en(grid-export)=22427.63kWh , Total_supply=50640.23kWh , self-consump.rate=55.7 , Grid_cost=€  1548.45 , Total_selling_cost=€  626.56 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6601.06 , Grid_used_en(grid-import)=1508.69kWh , Total_demand=53677.55kWh , autarky-rate=97.2 , RE-to-vehicle_unused_en(grid-export)=8109.75kWh , Total_supply=60278.6kWh , self-consump.rate=86.5 , Total_selling_cost=€  -245.76 , Grid_cost=€  70.23 
 EV_INFO: Av.EV_energy_leaving=kWh  72.3 , Std.EV_energy_leaving=kWh  22.93 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 410336.03 - Step_rewars (load_t= 351182.78, EVs_en

In [41]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
VPP_table.head(15000)

0    1          2    3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
...                        ...  ...        ...  ...                 ...   
2022-06-06 04:45:00  53.375015  0.0  99.989998  0.0  [6709, 0, 6708, 0]   
2022-06-06 05:00:00  53.125015  0.0  99.989998  0.0  [6709, 0, 6708, 0]   
2022-06-06 05:15:00  52.875015  0.0  99.989998  0.0  [6709, 0, 6708, 0]   
2022-06-06 05:30:00  52.625015  0.0  99.989998  0.0  [6709, 0, 6708, 0]   
2022-06-06 05:45:00  52.375015  0.0  99.989998  0.0  [6709, 0, 6708, 0]   

                          actions                   mask_truth  \
time                                                             
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True]   
...                           ...                          ...   
2022-06-06 04:45:00  [2, 0, 1, 2]  [False, True, False, False]   
2022-06-06 05:00:00  [2, 0, 1, 2]  [False, True, False, False]   
2022-06-06 05:15:00  [2, 0, 1, 2]  [False, True, False, False]   
2022-06-06 05:30:00  [2, 0, 1, 2]  [False, True, False, False]   
2022-06-06 05:45:00  [2, 0, 1, 2]  [False, True, False, False]   

                     ev_charged_pwr  ev_discharged_pwr       load  \
time                                                                
2022-01-01 00:00:00        0.000000                0.0  -4.193270   
2022-01-01 00:15:00        0.000000                0.0  -3.029498   
2022-01-01 00:30:00        0.000000                0.0  -3.839573   
2022-01-01 00:45:00        0.000000                0.0  -3.524186   
2022-01-01 01:00:00        0.000000                0.0  -3.957994   
...                             ...                ...        ...   
2022-06-06 04:45:00        0.000009               -1.0 -11.694288   
2022-06-06 05:00:00        0.000009               -1.0 -15.401101   
2022-06-06 05:15:00        0.000009               -1.0 -15.121538   
2022-06-06 05:30:00        0.000009               -1.0 -14.549609   
2022-06-06 05:45:00        0.000009               -1.0 -15.055198   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    -3.382497        0.0  -3.382497  
2022-01-01 00:15:00    -4.732622        0.0  -4.732622  
2022-01-01 00:30:00    -4.206976        0.0  -4.206976  
2022-01-01 00:45:00    -4.929990        0.0  -4.929990  
2022-01-01 01:00:00    -5.848668        0.0  -5.848668  
...                          ...        ...        ...  
2022-06-06 04:45:00   -15.401101        0.0 -15.401101  
2022-06-06 05:00:00   -15.121538        0.0 -15.121538  
2022-06-06 05:15:00   -14.590554        0.0 -14.590554  
2022-06-06 05:30:00   -15.055198        0.0 -15.055198  
2022-06-06 05:45:00   -15.404694        0.0 -15.404694  

[15000 rows x 13 columns]

In [43]:
#env.plot_VPP_results()


In [44]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [45]:
env.plot_VPP_Elvis_comparison()

In [46]:
#env.plot_rewards_results()

In [47]:
env.plot_rewards_stats()

In [48]:
env.plot_EVs_kpi()

In [49]:
env.plot_load_kpi()

In [50]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [51]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 11:00:00, Parking_time: 21.48190885011437, Leaving_time: 2022-01-02 08:28:54.871860, SOC: 0.5428144701863753, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 15:00:00, Parking_time: 23.274962549549578, Leaving_time: 2023-01-01 14:16:29.865178, SOC: 0.355338741913263, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8737.36 , Grid_used_en=kWh  31855.78 , RE-to-vehicle_unused_en=kWh  23118.41 , Total_selling_cost=€  485.42 , Grid_cost=€  1336.74 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [52]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7371.46 , Grid_used_en(grid-import)=31330.14kWh , Total_demand=57889.3kWh , autarky-rate=45.9 , RE-to-vehicle_unused_en(grid-export)=23958.68kWh , Total_supply=50517.84kWh , self-consump.rate=52.6 , Grid_cost=€  1315.82 , Total_selling_cost=€  448.47 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....


In [53]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [54]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8279.24 , Grid_used_en(grid-import)=31890.18kWh , Total_demand=58766.03kWh , autarky-rate=45.7 , RE-to-vehicle_unused_en(grid-export)=23610.94kWh , Total_supply=50486.79kWh , self-consump.rate=53.2 , Grid_cost=€  1342.78 , Total_selling_cost=€  489.17 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9640.37 , Grid_used_en(grid-import)=1246.41kWh , Total_demand=50277.57kWh , autarky-rate=97.5 , RE-to-vehicle_unused_en(grid-export)=10886.78kWh , Total_supply=59917.93kWh , self-consump.rate=81.8 , Total_selling_cost=€  -328.58 , Grid_cost=€  50.46 
 EV_INFO: Av.EV_energy_leaving=kWh  74.23 , Std.EV_energy_leaving=kWh  22.79 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 380310.45 - Step_rewars (load_t= 317968.13, EVs_e

In [55]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
VPP_table.head(14995)

0    1          2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [2, 0, 1, 0]   
...                  ...  ...        ...  ...              ...           ...   
2022-06-06 03:30:00  0.0  0.0  67.161736  0.0  [0, 0, 9827, 0]  [2, 0, 1, 2]   
2022-06-06 03:45:00  0.0  0.0  68.255508  0.0  [0, 0, 9827, 0]  [2, 0, 1, 2]   
2022-06-06 04:00:00  0.0  0.0  69.964828  0.0  [0, 0, 9827, 0]  [2, 0, 1, 2]   
2022-06-06 04:15:00  0.0  0.0  71.460197  0.0  [0, 0, 9827, 0]  [2, 0, 1, 2]   
2022-06-06 04:30:00  0.0  0.0  73.028610  0.0  [0, 0, 9827, 0]  [2, 0, 1, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [False, True, True, False]        3.881975   
2022-06-06 03:45:00   [False, True, True, False]        4.375084   
2022-06-06 04:00:00   [False, True, True, False]        6.837285   
2022-06-06 04:15:00   [False, True, True, False]        5.981465   
2022-06-06 04:30:00   [False, True, True, False]        6.273646   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -4.322526    -5.454514        0.0   
2022-01-01 00:15:00                0.0 -4.499965    -3.603378        0.0   
2022-01-01 00:30:00                0.0 -3.162027    -2.718178        0.0   
2022-01-01 00:45:00                0.0 -2.630907    -5.670503        0.0   
2022-01-01 01:00:00                0.0 -4.737553    -6.212651        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 03:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 04:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 04:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 04:30:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.454514  
2022-01-01 00:15:00  -3.603378  
2022-01-01 00:30:00  -2.718178  
2022-01-01 00:45:00  -5.670503  
2022-01-01 01:00:00  -6.212651  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  15.000000  
2022-06-06 04:30:00  15.000000  

[14995 rows x 13 columns]

In [57]:
env.plot_VPP_autarky()

In [58]:
#env.plot_VPP_results()

In [59]:
env.plot_VPP_supply_demand()

In [60]:
env.plot_VPP_Elvis_comparison()

In [61]:
#env.plot_rewards_results()

In [62]:
env.plot_rewards_stats()

In [63]:
env.plot_EVs_kpi()

In [64]:
env.plot_actions_kpi()

In [65]:
env.plot_load_kpi()

In [66]:
env.plot_yearly_load_log()

In [67]:
#env.close()